In [1]:
## acuity prediction gpt 4o 

In [2]:
import pandas as pd
pd.set_option('display.max_rows', None)  # Display all rows
pd.set_option('display.max_columns', None)  # Display all columns
pd.set_option('display.max_colwidth', None)  # Set max column width to None
pd.set_option('display.width', None)  # Set width to None

In [4]:
df = pd.read_csv('results.csv')

In [6]:
df.columns

Index(['Unnamed: 0', 'Unnamed: 0.1', 'Unnamed: 0.1.1', 'patientdurablekey',
       'encounterkey', 'ArrivalDateKey', 'DepartureDateKeyValue',
       'DepartureDateKey', 'DispositionDateKeyValue',
       'primarychiefcomplaintname', 'primaryeddiagnosisname', 'sex',
       'birthdate', 'firstrace', 'preferredlanguage',
       'highestlevelofeducation', 'maritalstatus', 'Age',
       'Discharge_Summary_Date', 'Discharge_Summary_Note_Key',
       'Progress_Note_Date', 'Progress_Note_Key', 'HP_Note_Date',
       'HP_Note_Key', 'Echo_Date', 'Echo_Key', 'Imaging_Date', 'Imaging_Key',
       'Consult_Date', 'Consult_Key', 'ED_Provider_Notes_Date',
       'ED_Provider_Notes_Key', 'ECG_Date', 'ECG_Key',
       'Discharge_Summary_Text', 'Progress_Note_Text', 'HP_Note_Text',
       'Echo_Text', 'Imaging_Text', 'Consult_Text', 'ECG_Text',
       'ED_Provider_Notes_Text', 'One_Sentence_Extracted', 'note_count',
       'acuitylevel', 'eddisposition'],
      dtype='object')

In [7]:
df['acuitylevel'].unique()

array(['Immediate', 'Urgent', 'Less Urgent', 'Emergent', '*Unspecified',
       'Non-Urgent', nan], dtype=object)

In [27]:
import re
import pandas as pd

# Function to extract vital signs with enhanced pattern matching
def extract_vital_signs_improved(text):
    if not isinstance(text, str):
        return "No vital signs available"
    
    # Try multiple patterns in order of specificity
    
    # Pattern 1: Standard format "Triage Vital Signs:" to "HENT:"
    pattern1 = r"Triage Vital Signs:.*?(?=HENT:)"
    match1 = re.search(pattern1, text, re.DOTALL)
    if match1:
        return match1.group(0).strip()
    
    # Pattern 2: Look for vital signs with various headers
    pattern2 = r"(?:Triage Vital Signs|Vital Signs)[\s:]*.*?(?=(?:HENT|Head|Eyes|Cardiovascular|Pulmonary|Constitutional|Physical Exam):)"
    match2 = re.search(pattern2, text, re.DOTALL)
    if match2:
        return match2.group(0).strip()
    
    # Pattern 3: Look for specific vital sign measurements
    vital_pattern = r"(?:BP|Heart Rate|Pulse|Temp|Resp|SpO2|Temperature)[\s:].{1,150}"
    vitals_found = re.findall(vital_pattern, text)
    if vitals_found:
        return "Vital Signs: " + " ".join(vitals_found)
    
    # Pattern 4: Any section with numeric values that might be vital signs
    numeric_pattern = r"(?:BP|HR|RR|T|Temp|O2)[\s:]*\d+(?:[\/\.\-]\d+)?(?:\s*[%℃℉]?)+"
    numeric_vitals = re.findall(numeric_pattern, text)
    if numeric_vitals:
        return "Vital Signs: " + " ".join(numeric_vitals)
    
    # Last resort: Check if there are any numbers that could be vital signs
    bp_pattern = r"\d{2,3}\/\d{2,3}"
    bp_found = re.search(bp_pattern, text)
    if bp_found:
        # Try to extract a reasonable context around potential BP
        context_start = max(0, bp_found.start() - 100)
        context_end = min(len(text), bp_found.end() + 100)
        return "Possible Vital Signs: " + text[context_start:context_end]
    
    # If absolutely nothing is found, return a standardized message
    return "No vital signs available"

# Apply the function to create a new column in the dataframe
df['Vital_Signs'] = df['ED_Provider_Notes_Text'].apply(extract_vital_signs_improved)

# Show the count of rows where vital signs were successfully extracted
extracted_count = df[df['Vital_Signs'] != "No vital signs available"].shape[0]
total_count = len(df)
print(f"Successfully extracted vital signs from {extracted_count} out of {total_count} rows ({extracted_count/total_count:.2%})")

Successfully extracted vital signs from 3977 out of 3977 rows (100.00%)


In [28]:
df['Vital_Signs']

0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              Triage Vital Signs:  BP: (!) 176/128, Heart Rate: (!) 148, Pulse - Palpated/Pleth: (!) 148, Temp: 37.6 °C

In [18]:
df.columns

Index(['Unnamed: 0', 'Unnamed: 0.1', 'Unnamed: 0.1.1', 'patientdurablekey',
       'encounterkey', 'ArrivalDateKey', 'DepartureDateKeyValue',
       'DepartureDateKey', 'DispositionDateKeyValue',
       'primarychiefcomplaintname', 'primaryeddiagnosisname', 'sex',
       'birthdate', 'firstrace', 'preferredlanguage',
       'highestlevelofeducation', 'maritalstatus', 'Age',
       'Discharge_Summary_Date', 'Discharge_Summary_Note_Key',
       'Progress_Note_Date', 'Progress_Note_Key', 'HP_Note_Date',
       'HP_Note_Key', 'Echo_Date', 'Echo_Key', 'Imaging_Date', 'Imaging_Key',
       'Consult_Date', 'Consult_Key', 'ED_Provider_Notes_Date',
       'ED_Provider_Notes_Key', 'ECG_Date', 'ECG_Key',
       'Discharge_Summary_Text', 'Progress_Note_Text', 'HP_Note_Text',
       'Echo_Text', 'Imaging_Text', 'Consult_Text', 'ECG_Text',
       'ED_Provider_Notes_Text', 'One_Sentence_Extracted', 'note_count',
       'acuitylevel', 'eddisposition', 'Vital_Signs'],
      dtype='object')

In [29]:
import pandas as pd
import os
import re
import json
import base64
import requests
import time
import urllib.parse

pd.set_option('display.max_rows', None)  # Display all rows
pd.set_option('display.max_columns', None)  # Display all columns
pd.set_option('display.max_colwidth', None)  # Set max column width to None
pd.set_option('display.width', None)  # Set width to None
# First, let's test by hard coding your Mulesoft Azure API key into the next line
API_KEY = 'MTEwMTQzZjI4MzBjNDY0MTgyMjUyMWE3MDAyZjQ4MTM6OGI3YUQzMDE1QTk0NDVmNDk3ZDNBYTVGOERGNjJFNDk='  ##### Paste your API key between the quotes #####
API_VERSION = '2024-06-01'  # For the most recent production release: https://learn.microsoft.com/en-us/azure/ai-services/openai/api-version-deprecation#latest-ga-api-release
RESOURCE_ENDPOINT = 'https://unified-api.ucsf.edu/general'  # no trailing slash--this is used by libraries as a partial URL
DEPLOYMENT_NAME = "gpt-4o-2024-08-06" 

In [34]:
import pandas as pd
import numpy as np
import requests
import time
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix
import matplotlib.pyplot as plt
import seaborn as sns
from tqdm import tqdm
import json

# Function to run acuity prediction with different input combinations
def predict_acuity(experiment_inputs, row):
    # Skip if any required field is missing
    for field in experiment_inputs:
        if field in row and pd.isna(row[field]):
            return None
    
    # Build the prompt based on experiment inputs
    prompt = "Predict the emergency department acuity level for this patient.\n\n"
    
    # Add information based on experiment inputs
    if "primarychiefcomplaintname" in experiment_inputs:
        prompt += f"Chief Complaint: {row['primarychiefcomplaintname']}\n"
    
    if "age" in experiment_inputs:
        prompt += f"Age: {row['Age']}\n"
    
    if "sex" in experiment_inputs:
        prompt += f"Sex: {row['sex']}\n"
    
    if "firstrace" in experiment_inputs:
        prompt += f"Race: {row['firstrace']}\n"
    
    if "Vital_Signs" in experiment_inputs and not pd.isna(row['Vital_Signs']):
        prompt += f"Vital Signs: {row['Vital_Signs']}\n"
    
    # Add instructions for output format
    prompt += "\nSelect the most appropriate acuity level from the following options ONLY:\n"
    prompt += "'Immediate', 'Emergent', 'Urgent', 'Less Urgent', 'Non-Urgent'\n\n"
    prompt += "Respond with ONLY ONE of these five options based on the information provided."
    
    # Setup API request
    url = f"{RESOURCE_ENDPOINT}/openai/deployments/{DEPLOYMENT_NAME}/chat/completions?api-version={API_VERSION}"
    
    headers = {
        "Content-Type": "application/json",
        "api-key": API_KEY
    }
    
    payload = {
        "messages": [
            {"role": "system", "content": "You are an experienced Emergency Department (ED) triage nurse with expertise in accurately assessing patient acuity levels based on clinical information."},
            {"role": "user", "content": prompt}
        ],
        "temperature": 0.1,
        "max_tokens": 50  # Short response needed
    }
    
    # Make API request with retries
    retries = 0
    while retries < 3:
        try:
            response = requests.post(url, headers=headers, json=payload)
            response.raise_for_status()
            
            # Extract and clean prediction
            prediction = response.json()["choices"][0]["message"]["content"].strip()
            
            # Handle potential variations in responses
            for acuity in ['Immediate', 'Emergent', 'Urgent', 'Less Urgent', 'Non-Urgent']:
                if acuity.lower() in prediction.lower():
                    return acuity
            
            # If no match found, return the raw response for debugging
            return prediction
            
        except requests.exceptions.RequestException as e:
            print(f"Request failed: {e}. Retrying {retries+1}/3...")
            time.sleep(5)  # Wait before retrying
            retries += 1
    
    return None  # Return None if all retries fail

# Function to evaluate model performance
def evaluate_acuity_predictions(true_labels, predicted_labels):
    # Filter out None values
    valid_indices = [i for i, pred in enumerate(predicted_labels) if pred is not None]
    filtered_true = [true_labels[i] for i in valid_indices]
    filtered_pred = [predicted_labels[i] for i in valid_indices]
    
    # Calculate accuracy
    accuracy = accuracy_score(filtered_true, filtered_pred)
    
    # Generate classification report
    report = classification_report(filtered_true, filtered_pred, output_dict=True)
    
    # Create confusion matrix
    cm = confusion_matrix(filtered_true, filtered_pred)
    
    return {
        'accuracy': accuracy,
        'classification_report': report,
        'confusion_matrix': cm,
        'processed_samples': len(filtered_true),
        'total_samples': len(true_labels),
        'sample_predictions': list(zip(filtered_true[:10], filtered_pred[:10]))  # Sample of predictions for review
    }

# Define experiments with progressive information
experiments = [
    {
        'name': 'Experiment 1: Chief Complaint and Vital signs',
        'inputs': ['primarychiefcomplaintname', 'Vital_Signs']
    },
    {
        'name': 'Experiment 2: Chief Complaint + age',
        'inputs': ['primarychiefcomplaintname', 'Vital_Signs','age']
    },
    {
        'name': 'Experiment 3: Chief Complaint + sex',
        'inputs': ['primarychiefcomplaintname', 'Vital_Signs', 'age', 'sex']
    },
    {
        'name': 'Experiment 4: All Information',
        'inputs': ['primarychiefcomplaintname', 'age', 'sex', 'firstrace', 'Vital_Signs']
    }
]

# Main function to run all experiments
def run_acuity_prediction_experiments(df, sample_size=None):
    # Sample data if specified (for faster testing)
    if sample_size and sample_size < len(df):
        df_sample = df.sample(sample_size, random_state=42)
    else:
        df_sample = df
    
    results = {}
    
    # Extract true labels
    true_acuity = df_sample['acuitylevel'].tolist()
    
    # Run each experiment
    for experiment in experiments:
        print(f"\nRunning {experiment['name']}...")
        
        # Make predictions
        predictions = []
        for _, row in tqdm(df_sample.iterrows(), total=len(df_sample)):
            prediction = predict_acuity(experiment['inputs'], row)
            predictions.append(prediction)
        
        # Evaluate results
        evaluation = evaluate_acuity_predictions(true_acuity, predictions)
        results[experiment['name']] = evaluation
        
        # Print immediate results
        print(f"Accuracy: {evaluation['accuracy']:.4f}")
        print(f"Processed {evaluation['processed_samples']} out of {evaluation['total_samples']} samples")
        print("Sample predictions (True, Predicted):")
        for true, pred in evaluation['sample_predictions'][:5]:
            print(f"  {true} -> {pred}")
    
    return results

# Function to visualize results
def visualize_results(results):
    # Plot accuracy comparison
    accuracies = [results[exp]['accuracy'] for exp in results]
    experiment_names = [exp.split(':')[0] for exp in results]
    
    plt.figure(figsize=(10, 6))
    bars = plt.bar(experiment_names, accuracies, color='skyblue')
    plt.ylim(0, 1.0)
    plt.ylabel('Accuracy')
    plt.title('Acuity Prediction Accuracy by Experiment')
    plt.xticks(rotation=45, ha='right')
    
    # Add accuracy values on top of bars
    for bar in bars:
        height = bar.get_height()
        plt.text(bar.get_x() + bar.get_width()/2., height + 0.01,
                f'{height:.3f}', ha='center', va='bottom')
    
    plt.tight_layout()
    plt.savefig('acuity_prediction_accuracy.png')
    plt.close()
    
    # Create confusion matrices for each experiment
    for exp_name, exp_results in results.items():
        plt.figure(figsize=(10, 8))
        cm = exp_results['confusion_matrix']
        unique_labels = sorted(list(set([label for label_list in exp_results['sample_predictions'] for label in label_list if label is not None])))
        
        sns.heatmap(cm, annot=True, fmt='d', cmap='Blues',
                   xticklabels=unique_labels,
                   yticklabels=unique_labels)
        plt.xlabel('Predicted')
        plt.ylabel('True')
        plt.title(f'Confusion Matrix - {exp_name}')
        plt.tight_layout()
        
        # Clean experiment name for filename
        clean_name = exp_name.split(':')[0].replace(' ', '_')
        plt.savefig(f'confusion_matrix_{clean_name}.png')
        plt.close()

# Save results to file
def save_results(results, filename='acuity_prediction_results.json'):
    # Convert numpy arrays to lists for JSON serialization
    serializable_results = {}
    
    for exp_name, exp_results in results.items():
        serializable_exp = exp_results.copy()
        
        # Convert confusion matrix to list
        serializable_exp['confusion_matrix'] = exp_results['confusion_matrix'].tolist()
        
        # Convert classification report (already a dict but might contain numpy values)
        report = {}
        for label, metrics in exp_results['classification_report'].items():
            if isinstance(metrics, dict):
                report[label] = {k: float(v) for k, v in metrics.items()}
            else:
                report[label] = float(metrics)
        serializable_exp['classification_report'] = report
        
        serializable_results[exp_name] = serializable_exp
    
    # Save to file
    with open(filename, 'w') as f:
        json.dump(serializable_results, f, indent=2)

# Main execution
if __name__ == "__main__":
    # Load your data
    print("Loading data...")
    
    # Print unique acuity levels for verification
    print("Unique acuity levels in data:")
    print(df['acuitylevel'].value_counts())
    
    # Run experiments on a small sample first for testing
    sample_size = None  # Adjust as needed, None for full dataset
    
    results = run_acuity_prediction_experiments(df, sample_size)
    visualize_results(results)
    save_results(results)
    
    print("\nExperiment results:")
    for exp_name, exp_results in results.items():
        print(f"\n{exp_name}")
        print(f"Accuracy: {exp_results['accuracy']:.4f}")
        print(f"Processed samples: {exp_results['processed_samples']} / {exp_results['total_samples']}")
    
    print("\nResults saved to 'acuity_prediction_results.json'")
    print("Visualizations saved as PNG files.")

Loading data...
Unique acuity levels in data:
Urgent         2180
Emergent       1619
Less Urgent     137
Immediate        20
Non-Urgent       14
Name: acuitylevel, dtype: int64

Running Experiment 1: Chief Complaint and Vital signs...


100%|██████████| 3977/3977 [45:43<00:00,  1.45it/s]  
/usr/local/icsoftware/anaconda3/envs/jupyterhub_base_v1.5/lib/python3.7/site-packages/sklearn/metrics/_classification.py:1221: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Accuracy: 0.6236
Processed 3977 out of 3977 samples
Sample predictions (True, Predicted):
  Immediate -> Immediate
  Urgent -> Urgent
  Less Urgent -> Urgent
  Urgent -> Urgent
  Urgent -> Emergent

Running Experiment 2: Chief Complaint + age...


100%|██████████| 3977/3977 [45:40<00:00,  1.45it/s]  


Accuracy: 0.6213
Processed 3977 out of 3977 samples
Sample predictions (True, Predicted):
  Immediate -> Immediate
  Urgent -> Urgent
  Less Urgent -> Urgent
  Urgent -> Urgent
  Urgent -> Emergent

Running Experiment 3: Chief Complaint + sex...


...

Accuracy: 0.6238
Processed 3977 out of 3977 samples
Sample predictions (True, Predicted):
  Immediate -> Immediate
  Urgent -> Urgent
  Less Urgent -> Urgent
  Urgent -> Urgent
  Urgent -> Emergent

Running Experiment 4: All Information...


 88%|████████▊ | 3486/3977 [39:54<07:52,  1.04it/s]  

Request failed: ('Connection aborted.', ConnectionResetError(104, 'Connection reset by peer')). Retrying 1/3...


 92%|█████████▏| 3639/3977 [7:17:26<40:37,  7.21s/it]


KeyboardInterrupt: 

In [35]:
## experiment 4 timed out
import pandas as pd
import requests
import time
import random
import os
from tqdm import tqdm
import json


# Function to predict acuity with robust error handling
def predict_acuity_with_all_info(row, max_retries=5):
    """
    Predicts acuity level using all available information with robust error handling.
    """
    # Skip if any critical field is missing
    required_fields = ['primarychiefcomplaintname']
    for field in required_fields:
        if field not in row or pd.isna(row[field]):
            return None
    
    # Build the prompt with all available information
    prompt = "Predict the emergency department acuity level for this patient.\n\n"
    
    # Add chief complaint (required)
    prompt += f"Chief Complaint: {row['primarychiefcomplaintname']}\n"
    
    # Add optional fields if available
    if 'age' in row and not pd.isna(row['age']):
        prompt += f"Age: {row['age']}\n"
    
    if 'sex' in row and not pd.isna(row['sex']):
        prompt += f"Sex: {row['sex']}\n"
    
    if 'firstrace' in row and not pd.isna(row['firstrace']):
        prompt += f"Race: {row['firstrace']}\n"
    
    if 'Vital_Signs' in row and not pd.isna(row['Vital_Signs']):
        # Limit vital signs to 300 characters to reduce payload size
        vital_signs = str(row['Vital_Signs'])
        if len(vital_signs) > 300:
            vital_signs = vital_signs[:300] + "..."
        prompt += f"Vital Signs: {vital_signs}\n"
    
    # Add instructions for output format
    prompt += "\nSelect the most appropriate acuity level from the following options ONLY:\n"
    prompt += "'Immediate', 'Emergent', 'Urgent', 'Less Urgent', 'Non-Urgent'\n\n"
    prompt += "Respond with ONLY ONE of these five options."
    
    # API request with retries and backoff
    current_retry = 0
    backoff_time = 2  # Initial backoff in seconds
    
    while current_retry <= max_retries:
        try:
            url = f"{RESOURCE_ENDPOINT}/openai/deployments/{DEPLOYMENT_NAME}/chat/completions?api-version={API_VERSION}"
            
            headers = {
                "Content-Type": "application/json",
                "api-key": API_KEY
            }
            
            payload = {
                "messages": [
                    {"role": "system", "content": "You are an experienced Emergency Department triage nurse."},
                    {"role": "user", "content": prompt}
                ],
                "temperature": 0.1,
                "max_tokens": 50
            }
            
            # Use increased timeout
            response = requests.post(url, headers=headers, json=payload, timeout=60)
            response.raise_for_status()
            
            # Extract and clean prediction
            prediction = response.json()["choices"][0]["message"]["content"].strip()
            
            # Handle potential variations in responses
            for acuity in ['Immediate', 'Emergent', 'Urgent', 'Less Urgent', 'Non-Urgent']:
                if acuity.lower() in prediction.lower():
                    return acuity
            
            # If no match found, return the raw response for debugging
            return prediction
            
        except requests.exceptions.RequestException as e:
            current_retry += 1
            
            if current_retry > max_retries:
                print(f"Failed after {max_retries} retries: {e}")
                return "Prediction failed"
            
            # Log the error and retry info
            print(f"Request failed: {e}. Retrying {current_retry}/{max_retries} after {backoff_time} seconds...")
            
            # Implement exponential backoff with jitter
            time.sleep(backoff_time + random.uniform(0, 1))
            backoff_time *= 2  # Double the backoff time for next retry
    
    return "Prediction failed"

# Process data in batches with checkpointing
def process_with_checkpoints(df, batch_size=20, checkpoint_file="acuity_predictions_all_info.csv"):
    # Check if checkpoint exists
    if os.path.exists(checkpoint_file):
        processed_df = pd.read_csv(checkpoint_file)
        # Create a set of already processed encounter IDs for faster lookups
        if 'encounterkey' in processed_df.columns:
            processed_ids = set(processed_df['encounterkey'].tolist())
        else:
            # If no encounterkey column, use row indices
            processed_ids = set(range(len(processed_df)))
        print(f"Resuming from checkpoint with {len(processed_ids)} already processed records")
    else:
        processed_df = pd.DataFrame(columns=df.columns.tolist() + ['predicted_acuity'])
        processed_ids = set()
    
    # Calculate total batches
    total_records = len(df)
    total_batches = (total_records + batch_size - 1) // batch_size
    
    # Track overall progress
    processed_count = len(processed_ids)
    start_time = time.time()
    
    # Process in batches
    for batch_num in range(total_batches):
        start_idx = batch_num * batch_size
        end_idx = min(start_idx + batch_size, total_records)
        
        # Get current batch
        batch = df.iloc[start_idx:end_idx].copy()
        
        # Filter out already processed records
        if 'encounterkey' in batch.columns:
            batch = batch[~batch['encounterkey'].isin(processed_ids)]
        else:
            batch = batch.iloc[[i for i in range(start_idx, end_idx) if i not in processed_ids]]
        
        if len(batch) == 0:
            continue
        
        print(f"Processing batch {batch_num+1}/{total_batches}, records {start_idx}-{end_idx}")
        
        # Process each record in batch
        for idx, row in tqdm(batch.iterrows(), total=len(batch)):
            # Make prediction
            prediction = predict_acuity_with_all_info(row)
            
            # Add prediction to row
            row_copy = row.copy()
            row_copy['predicted_acuity'] = prediction
            
            # Append to results dataframe
            processed_df = pd.concat([processed_df, pd.DataFrame([row_copy])], ignore_index=True)
            
            # Mark as processed
            if 'encounterkey' in row:
                processed_ids.add(row['encounterkey'])
            else:
                processed_ids.add(idx)
            
            # Update progress count
            processed_count += 1
        
        # Save checkpoint after each batch
        processed_df.to_csv(checkpoint_file, index=False)
        
        # Calculate and display progress statistics
        elapsed_time = time.time() - start_time
        records_per_second = processed_count / elapsed_time if elapsed_time > 0 else 0
        estimated_remaining = (total_records - processed_count) / records_per_second if records_per_second > 0 else float('inf')
        
        print(f"Progress: {processed_count}/{total_records} records ({processed_count/total_records:.1%})")
        print(f"Speed: {records_per_second:.2f} records/second")
        print(f"Est. time remaining: {estimated_remaining/60:.1f} minutes")
        print(f"Checkpoint saved at: {checkpoint_file}")
        
        # Add a short pause between batches to be nice to the API
        time.sleep(2)
    
    return processed_df

# Calculate accuracy
def calculate_accuracy(df):
    # Filter out rows with failed predictions
    valid_df = df[df['predicted_acuity'].isin(['Immediate', 'Emergent', 'Urgent', 'Less Urgent', 'Non-Urgent'])]
    
    # Count matches
    matches = (valid_df['predicted_acuity'] == valid_df['acuitylevel']).sum()
    total = len(valid_df)
    
    accuracy = matches / total if total > 0 else 0
    print(f"Accuracy: {matches}/{total} = {accuracy:.4f} ({accuracy:.2%})")
    
    # Count by acuity level
    print("\nAccuracy by acuity level:")
    for level in ['Immediate', 'Emergent', 'Urgent', 'Less Urgent', 'Non-Urgent']:
        level_df = valid_df[valid_df['acuitylevel'] == level]
        if len(level_df) > 0:
            level_matches = (level_df['predicted_acuity'] == level_df['acuitylevel']).sum()
            level_accuracy = level_matches / len(level_df)
            print(f"{level}: {level_matches}/{len(level_df)} = {level_accuracy:.4f} ({level_accuracy:.2%})")
    
    return accuracy

# Main execution
if __name__ == "__main__":
    # Load the data
    print("Loading data...")
    
    print(f"Loaded {len(df)} records")
    print("Starting prediction process with all information...")
    
    # Run the prediction with all information
    results_df = process_with_checkpoints(df)
    
    # Calculate and display accuracy
    accuracy = calculate_accuracy(results_df)
    
    # Save final results
    final_output = "acuity_prediction_results_all_info.csv"
    results_df.to_csv(final_output, index=False)
    print(f"Final results saved to {final_output}")

Loading data...
Loaded 3977 records
Starting prediction process with all information...
Processing batch 1/199, records 0-20


100%|██████████| 20/20 [00:14<00:00,  1.39it/s]


Progress: 20/3977 records (0.5%)
Speed: 1.38 records/second
Est. time remaining: 47.8 minutes
Checkpoint saved at: acuity_predictions_all_info.csv
Processing batch 2/199, records 20-40


100%|██████████| 20/20 [00:19<00:00,  1.05it/s]


Progress: 40/3977 records (1.0%)
Speed: 1.12 records/second
Est. time remaining: 58.6 minutes
Checkpoint saved at: acuity_predictions_all_info.csv
Processing batch 3/199, records 40-60


...

Progress: 3940/3977 records (99.1%)
Speed: 1.03 records/second
Est. time remaining: 0.6 minutes
Checkpoint saved at: acuity_predictions_all_info.csv
Processing batch 198/199, records 3940-3960


100%|██████████| 20/20 [00:13<00:00,  1.46it/s]


Progress: 3960/3977 records (99.6%)
Speed: 1.03 records/second
Est. time remaining: 0.3 minutes
Checkpoint saved at: acuity_predictions_all_info.csv
Processing batch 199/199, records 3960-3977


100%|██████████| 17/17 [00:11<00:00,  1.50it/s]


Progress: 3977/3977 records (100.0%)
Speed: 1.03 records/second
Est. time remaining: 0.0 minutes
Checkpoint saved at: acuity_predictions_all_info.csv
Accuracy: 2465/3977 = 0.6198 (61.98%)

Accuracy by acuity level:
Immediate: 5/20 = 0.2500 (25.00%)
Emergent: 857/1619 = 0.5293 (52.93%)
Urgent: 1603/2180 = 0.7353 (73.53%)
Less Urgent: 0/137 = 0.0000 (0.00%)
Non-Urgent: 0/14 = 0.0000 (0.00%)
Final results saved to acuity_prediction_results_all_info.csv
